<a href="https://colab.research.google.com/github/nikolina-p/NLP-with-Transformers/blob/main/Making_my_dataset.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## **Gutenberg preprocessing**
Original dataset: manu/project_gutenberg

It took ~15min on Colab CPU HighRAM environment to download the manu/gutenberg dataset, clean it and make 39 parquet files.

It took ~5min to upload parquet files to Hub.


---
It took 40 min to download the manu/gutenberg dataset, clean it (2 additional cleaning functions), tokenize it and save into 39 parquet files.

Tokenized dataset is 15GB.

Uploading takes about 5-10 min.


- total num tokens (from main notebook):

100%|██████████| 38026/38026 [23:34<00:00, 26.88it/s]Total number of tokens: 3638561697


In [ ]:
%%capture
!pip install --upgrade huggingface_hub

In [ ]:
#@title Huggingface Hub login
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
#@title Upload parquet dataset to Huggingface Hub
from huggingface_hub import HfApi, Repository
import shutil
import os

hf_repo_name = "nikolina-p/gutenberg_clean_en"
local_dir = "deduplicated_dataset_by_id"

def upload_to_hf(repo_name, local_dir):
    # Create a new dataset repo on Huggingface
    api = HfApi()
    api.create_repo(repo_name, repo_type="dataset", exist_ok=True)

    # Clone the repo
    repo = Repository(local_dir="repo_tmp", clone_from=repo_name, repo_type="dataset")

    shutil.copytree(local_dir, os.path.join(repo.local_dir, "data"), dirs_exist_ok=True)

    repo.push_to_hub(commit_message="Initial upload of dataset")


## **Gutenberg: clean, tokenized, splits**

In [ ]:
import os
from datasets import load_dataset
import pyarrow as pa
import pyarrow.parquet as pq
from tqdm import tqdm

In [ ]:
#@title text cleaning functions
import re

def strip_gutenberg_header_footer(text):
    # remove header before ***START ...*** or *** START ... ***
    start_match = re.search(r"\*{3}\s*START[^*]*\*{3}", text, re.IGNORECASE)
    if start_match:
        text = text[start_match.end():]

    # remove footer after ***END ...*** or *** END ...***
    end_match = re.search(r"\*{3}\s*END[^*]*\*{3}", text, re.IGNORECASE)
    if end_match:
        text = text[:end_match.start()]
    return text.strip()

def clean_newlines(text):
    # replace 3 or more newlines with 2 newlines (paragraph break)
    return re.sub(r'\n{3,}', '\n\n', text)

def replace_single_newlines(text):
    # replace exactly one newline (\n) with a single space
    return re.sub(r'(?<!\n)\n(?!\n)', ' ', text)

def clean_spaces(text):
    # replace 2 or more spaces with a single space
    return re.sub(r' {2,}', ' ', text)

def preprocess(text):
    text = strip_gutenberg_header_footer(text)
    text = clean_newlines(text)
    text = clean_spaces(text)
    text = replace_single_newlines(text)
    return text

In [ ]:
#@title Download dataset, apply cleaning and save parquet files

import tiktoken

ds_gutenberg = load_dataset("manu/project_gutenberg", split="en", streaming=True)

seen_ids = set()
buffer = []
shard_size = 1000
shard_idx = 0
counter = 0
total = 0

output_dir = "cleaned_dataset"
os.makedirs(output_dir, exist_ok=True)

tokenizer = tiktoken.get_encoding("gpt2")
try:
    for example in tqdm(ds_gutenberg):
        total += 1
        row_id = example["id"]
        if row_id not in seen_ids:
            seen_ids.add(row_id)

            # inform about extra large books
            no_char = len(example["text"])
            if no_char >= 1_500_000:
                print(f"Book {total}, id {example['id']}, length {no_char} characters.")

            example["text"] = preprocess(example["text"])
            example["tokenized"] = tokenizer.encode(example["text"], allowed_special={"<|endoftext|>"})
            buffer.append(example)

            counter += 1

            if len(buffer) >= shard_size:
                table = pa.Table.from_pylist(buffer)
                pq.write_table(table, os.path.join(output_dir, f"shard-{shard_idx:03d}.parquet"))
                buffer = []
                shard_idx += 1
except KeyboardInterrupt:
    print("Keboard Interrupted")
# Write remaining buffer
if buffer:
    table = pa.Table.from_pylist(buffer)
    pq.write_table(table, os.path.join(output_dir, f"shard-{shard_idx:03d}.parquet"))
    print("END OF DATASET")

print(f"Total examples {total}")



Resolving data files:   0%|          | 0/52 [00:00<?, ?it/s]

67it [00:04, 35.20it/s]

Book 70, id 56673-0, length 1650422 characters.


79it [00:05, 20.89it/s]

Book 81, id 65236-0, length 1501473 characters.


...

Book 61284, id 53360-0, length 3487078 characters.


61296it [46:26,  1.27it/s]

Book 61297, id 10900-8, length 4363592 characters.


61340it [46:28, 21.99it/s]


END OF DATASET
Total examples 61340


In [ ]:
#@title Organize parquet files in train, validation and test splits
import os
import shutil

parquet_dir = "cleaned_dataset"
parquet_files = sorted(f for f in os.listdir(parquet_dir) if f.endswith(".parquet"))

n = len(parquet_files)
train_files = parquet_files[:int(0.85 * n)]
val_files   = parquet_files[int(0.85 * n):int(0.95 * n)]
test_files  = parquet_files[int(0.95 * n):]

split_dir = "split_dataset"
for split in ["train", "validation", "test"]:
    os.makedirs(os.path.join(split_dir, split), exist_ok=True)

# Copy files
for fname in train_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(split_dir, "train", fname))
for fname in val_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(split_dir, "validation", fname))
for fname in test_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(split_dir, "test", fname))



In [ ]:
!du -sh split_dataset/

15G	split_dataset/


In [ ]:
# inspecting parquet files
import pyarrow.parquet as pq

parquet_dir = "split_dataset/train"
parquet_files = [f for f in os.listdir(parquet_dir)]

table = pq.read_table(os.path.join(parquet_dir, parquet_files[0]))
print(table.schema)
print(table.num_rows)
print(table.to_pandas().head())

id: string
text: string
tokenized: list<element: int64>
  child 0, element: int64
1000
        id                                               text  \
0  31764-8  Produced by David Garcia, Joseph R. Hauser and...   
1  11805-8  Produced by Michael Dyck, Charles Franks, pour...   
2  55473-0  Produced by Marc D'Hooghe at Free Literature (...   
3  42787-8  Produced by Charlene Taylor, Jonathan Ingram, ...   
4  28177-8  Produced by Chris Curnow, Lindy Walsh, Greg Be...   

                                           tokenized  
0  [11547, 771, 416, 3271, 18555, 11, 7212, 371, ...  
1  [11547, 771, 416, 3899, 23524, 694, 11, 7516, ...  
2  [11547, 771, 416, 13067, 360, 6, 28900, 519, 2...  
3  [11547, 771, 416, 6258, 1734, 8121, 11, 11232,...  
4  [11547, 771, 416, 5180, 327, 700, 322, 11, 932...  


In [ ]:
# load local datastet
from datasets import load_dataset

parquet_files_test = [f for f in os.listdir("split_dataset/test")]
ds = load_dataset("parquet", data_files=[os.path.join("split_dataset/test", f) for f in parquet_files_test])
print(ds)

Generating train split: 0 examples [00:00, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'tokenized'],
        num_rows: 1026
    })
})


In [ ]:
#@title Loading uploaded tokenized dataset gutenberg_clean_tokenized_en_splits
from datasets import load_dataset

ds = load_dataset("nikolina-p/gutenberg_clean_tokenized_en_splits", split="train", streaming=True)

stream = iter(ds)
print(next(stream)['text'][:50])

Resolving data files:   0%|          | 0/33 [00:00<?, ?it/s]

E-text prepared by the Online Distributed Proofrea


In [ ]:
from datasets import load_dataset

ds = load_dataset("nikolina-p/gutenberg_clean_tokenized_en", split="train", streaming=True)

print(next(iter(ds)))

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

{'id': '41496-8', 'text': 'E-text prepared by the Online Distributed Proofreading Team (http://www.pgdp.net) from page images generously made available by Internet Archive (http://archive.org)\n\nNote: Images of the original pages are available through  Internet Archive. See  http://archive.org/details/addison_00cour\n\nTranscriber\'s note:\n\n Text enclosed by underscores is in italics (_italics_).\n\n Text enclosed by curly brackets is superscripted  (example: y{e}).\n\nEnglish Men of Letters\n\nEdited by John Morley\n\nADDISON\n\nby\n\nW. J. COURTHOPE\n\nHarper & Brothers Publishers New York and London 1902\n\n * * * * *\n\nENGLISH MEN OF LETTERS.\n\nEDITED BY JOHN MORLEY.\n\n JOHNSON Leslie Stephen.  GIBBON J. C. Morison.  SCOTT R. H. Hutton.  SHELLEY J. A. Symonds.  HUME T. H. Huxley.  GOLDSMITH William Black.  DEFOE William Minto.  BURNS J. C. Shairp.  SPENSER R. W. Church.  THACKERAY Anthony Trollope.  BURKE John Morley.  MILTON Mark Pattison.  HAWTHORNE Henry James, Jr.  SOUTHE

## **Gutenberg: clean and splits**

In [ ]:
from datasets import load_dataset, DownloadConfig
import os
from tqdm import tqdm
import shutil

In [ ]:
#@title download shards
os.makedirs("my_dataset_cache", exist_ok=True)

for i in range(39):
    url = f"https://huggingface.co/datasets/nikolina-p/gutenberg_clean_en/resolve/main/data/shard-{i:03d}.parquet"
    !wget -P /content/my_dataset_cache/ {url}
    # os.system(f"wget -P /content {url}")


--2025-08-19 21:16:59--  https://huggingface.co/datasets/nikolina-p/gutenberg_clean_en/resolve/main/data/shard-000.parquet
Resolving huggingface.co (huggingface.co)... 3.170.185.33, 3.170.185.14, 3.170.185.35, ...
Connecting to huggingface.co (huggingface.co)|3.170.185.33|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.hf.co/repos/43/94/4394ce560c8ef6e208a04840c798f42f6b223d7d3bc3d76c5345ef772ccb7d70/e2c3d2eb968e35413d0a889bee25b60cdeb534a7de4881d31534d2414c19d193?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27shard-000.parquet%3B+filename%3D%22shard-000.parquet%22%3B&Expires=1755641820&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTc1NTY0MTgyMH19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmhmLmNvL3JlcG9zLzQzLzk0LzQzOTRjZTU2MGM4ZWY2ZTIwOGEwNDg0MGM3OThmNDJmNmIyMjNkN2QzYmMzZDc2YzUzNDVlZjc3MmNjYjdkNzAvZTJjM2QyZWI5NjhlMzU0MTNkMGE4ODliZWUyNWI2MGNkZWI1MzRhN2RlNDg4MWQzMTUzNGQyNDE0YzE5

In [ ]:
#@title split shards into train, validation and test splits
parquet_dir = "my_dataset_cache"
parquet_files = sorted(f for f in os.listdir(parquet_dir) if f.endswith(".parquet"))
n = len(parquet_files)
train_files = parquet_files[:int(0.85 * n)]
val_files   = parquet_files[int(0.85 * n):int(0.95 * n)]
test_files  = parquet_files[int(0.95 * n):]

dataset_dir = os.makedirs("new_dir", exist_ok=True)
new_dir = "new_dir"
for split in ["train", "validation", "test"]:
    os.makedirs(os.path.join(new_dir, split), exist_ok=True)

# Copy files
for fname in train_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "train", fname))
for fname in val_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "validation", fname))
for fname in test_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "test", fname))

In [ ]:
#@title upload dataset to HF Hub (LOGIN TO HUB FIRST)
upload_to_hf("nikolina-p/gutenberg_clean_en_splits", "new_dir")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/datasets/nikolina-p/gutenberg_clean_en_splits into local empty directory.


Upload file data/train/shard-008.parquet:   0%|          | 1.00/235M [00:00<?, ?B/s]

Upload file data/train/shard-009.parquet:   0%|          | 1.00/235M [00:00<?, ?B/s]

Upload file data/train/shard-015.parquet:   0%|          | 1.00/234M [00:00<?, ?B/s]

Upload file data/train/shard-000.parquet:   0%|          | 1.00/234M [00:00<?, ?B/s]

...

Upload file data/validation/shard-033.parquet:   0%|          | 1.00/213M [00:00<?, ?B/s]

Upload file data/validation/shard-036.parquet:   0%|          | 1.00/211M [00:00<?, ?B/s]

Upload file data/train/shard-032.parquet:   0%|          | 1.00/207M [00:00<?, ?B/s]

Upload file data/test/shard-038.parquet:   0%|          | 1.00/8.95M [00:00<?, ?B/s]

To https://huggingface.co/datasets/nikolina-p/gutenberg_clean_en_splits
   e6c5a59..5e2d89a  main -> main

   e6c5a59..5e2d89a  main -> main



In [ ]:
dss = load_dataset("nikolina-p/gutenberg_clean_en_splits", split="test", streaming=True)

README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/33 [00:00<?, ?it/s]

In [ ]:
books_test = []
for book in tqdm(dss):
    books_test.append(book['id'])

1026it [00:04, 212.20it/s]


In [ ]:
len(books_test)

1026

In [ ]:
valid = load_dataset("nikolina-p/gutenberg_clean_en_splits", split="validation", streaming=True)

Resolving data files:   0%|          | 0/33 [00:00<?, ?it/s]

In [ ]:
books_valid = []
for book in tqdm(valid):
    books_valid.append(book['id'])

4000it [00:12, 326.02it/s]


## **Mini Gutenberg: clean and tokenized**

In [ ]:
#load the dataset
from datasets import load_dataset

ds = load_dataset('nikolina-p/gutenberg_clean_en', split='train', streaming=True)


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

In [ ]:
#@title Making Mini Gutenberg clean
#read text and split it on 2, 3, 1.5, 5, 2.5 out of 14 proportion and save in parquet file
stream = iter(ds)
splits = [(0, 2), (2, 5), (5, 6.5), (6.5, 11.5), (11.5, 14)]

output_dir = "local_data"
os.makedirs(output_dir, exist_ok=True)

buffer = []
shard_idx = 0
while shard_idx < 39:
    if len(buffer) <3:
        book = next(stream)
        l = len(book['text'])

        buffer.extend(
            {
                'id': book['id'],
                'text':book['text'][int(s*(l+13)/14):int(e*((l+13)/14))]
            }
            for (s, e) in splits
        )

    table = pa.Table.from_pylist(buffer[:3])
    del buffer[:3]
    pq.write_table(table, os.path.join(output_dir, f"shard-{shard_idx:03d}.parquet"))
    shard_idx += 1


In [ ]:
mini = load_dataset('local_data')
mini

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'text'],
        num_rows: 117
    })
})

In [ ]:
for e in mini['train']:
    print(f"{e['id']} : {len(e['text'])} characters")

41496-8 : 47843 characters
41496-8 : 71764 characters
41496-8 : 35883 characters
41496-8 : 119608 characters
41496-8 : 59791 characters
7529-0 : 43360 characters
7529-0 : 65041 characters
7529-0 : 32520 characters
7529-0 : 108401 characters
7529-0 : 54188 characters
25056-8 : 4696 characters
25056-8 : 7045 characters
25056-8 : 3522 characters
25056-8 : 11742 characters
25056-8 : 5858 characters
48941-8 : 85943 characters
48941-8 : 128915 characters
48941-8 : 64458 characters
48941-8 : 214859 characters
48941-8 : 107417 characters
35338-8 : 122240 characters
35338-8 : 183362 characters
35338-8 : 91680 characters
35338-8 : 305602 characters
35338-8 : 152789 characters
21060-8 : 81730 characters
21060-8 : 122596 characters
21060-8 : 61298 characters
21060-8 : 204326 characters
21060-8 : 102151 characters
22782-8 : 15054 characters
22782-8 : 22582 characters
22782-8 : 11291 characters
22782-8 : 37636 characters
22782-8 : 18806 characters
38207-0 : 24966 characters
38207-0 : 37450 character

In [ ]:
# upload to the hub
upload_to_hf("nikolina-p/mini_gutenberg", "local_data")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/datasets/nikolina-p/mini_gutenberg into local empty directory.


Upload file data/shard-007.parquet:   9%|9         | 32.0k/354k [00:00<?, ?B/s]

Upload file data/shard-009.parquet:  15%|#4        | 32.0k/220k [00:00<?, ?B/s]

Upload file data/shard-026.parquet:  10%|#         | 32.0k/314k [00:00<?, ?B/s]

Upload file data/shard-025.parquet:  12%|#1        | 32.0k/272k [00:00<?, ?B/s]

...

Upload file data/shard-003.parquet:  78%|#######8  | 32.0k/41.0k [00:00<?, ?B/s]

Upload file data/shard-027.parquet:  94%|#########3| 32.0k/34.1k [00:00<?, ?B/s]

Upload file data/shard-010.parquet: 100%|##########| 31.3k/31.3k [00:00<?, ?B/s]

Upload file data/shard-004.parquet: 100%|##########| 13.7k/13.7k [00:00<?, ?B/s]

To https://huggingface.co/datasets/nikolina-p/mini_gutenberg
   4d8f7c9..9018eea  main -> main

   4d8f7c9..9018eea  main -> main



In [ ]:
mini_hf = load_dataset('nikolina-p/mini_gutenberg', split='train', streaming=True)
mini_stream = iter(mini_hf)

next(mini_stream)

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

{'id': '41496-8',
 'text': 'E-text prepared by the Online Distributed Proofreading Team (http://www.pgdp.net) from page images generously made available by Internet Archive (http://archive.org)\n\nNote: Images of the original pages are available through  Internet Archive. See  http://archive.org/details/addison_00cour\n\nTranscriber\'s note:\n\n Text enclosed by underscores is in italics (_italics_).\n\n Text enclosed by curly brackets is superscripted  (example: y{e}).\n\nEnglish Men of Letters\n\nEdited by John Morley\n\nADDISON\n\nby\n\nW. J. COURTHOPE\n\nHarper & Brothers Publishers New York and London 1902\n\n * * * * *\n\nENGLISH MEN OF LETTERS.\n\nEDITED BY JOHN MORLEY.\n\n JOHNSON Leslie Stephen.  GIBBON J. C. Morison.  SCOTT R. H. Hutton.  SHELLEY J. A. Symonds.  HUME T. H. Huxley.  GOLDSMITH William Black.  DEFOE William Minto.  BURNS J. C. Shairp.  SPENSER R. W. Church.  THACKERAY Anthony Trollope.  BURKE John Morley.  MILTON Mark Pattison.  HAWTHORNE Henry James, Jr.  SOUTH

In [ ]:
from datasets import load_dataset

mini_hf = load_dataset('nikolina-p/mini_gutenberg', split='train')
books = set()
for book in mini_hf:
    books.add(book['id'])

len(books)

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

24

In [ ]:
mini_hf

Dataset({
    features: ['id', 'text'],
    num_rows: 117
})

In [ ]:
#@title Making Mini Gutenberg TOKENIZED
#read text and split it on 2, 3, 1.5, 5, 2.5 out of 14 proportion and save in parquet file
import tiktoken
tokenizer = tiktoken.get_encoding("gpt2")

stream = iter(ds)
splits = [(0, 2), (2, 5), (5, 6.5), (6.5, 11.5), (11.5, 14)]

output_dir = "local_data"
os.makedirs(output_dir, exist_ok=True)

buffer = []
shard_idx = 0
while shard_idx < 39:
    if len(buffer) <3:
        # add pieces of next book to buffer
        book = next(stream)
        l = len(book['text'])
        for (s, e) in splits:
            text = book['text'][int(s*(l+13)/14):int(e*((l+13)/14))]
            buffer.append(
                {
                    'id': book['id'],
                    'text':text,
                    'tokenized':tokenizer.encode(text)
                }
            )

    table = pa.Table.from_pylist(buffer[:3])
    del buffer[:3]
    pq.write_table(table, os.path.join(output_dir, f"shard-{shard_idx:03d}.parquet"))
    shard_idx += 1


In [ ]:
mini_tok = load_dataset("local_data")
mini_tok

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'tokenized'],
        num_rows: 117
    })
})

In [ ]:
# upload to the hub
upload_to_hf("nikolina-p/mini_gutenberg_tokenized", "local_data")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/datasets/nikolina-p/mini_gutenberg_tokenized into local empty directory.


Upload file data/shard-007.parquet:   5%|5         | 32.0k/622k [00:00<?, ?B/s]

Upload file data/shard-025.parquet:   7%|6         | 32.0k/492k [00:00<?, ?B/s]

Upload file data/shard-006.parquet:   6%|6         | 32.0k/495k [00:00<?, ?B/s]

Upload file data/shard-026.parquet:   6%|5         | 32.0k/567k [00:00<?, ?B/s]

...

Upload file data/shard-003.parquet:  41%|####1     | 32.0k/77.4k [00:00<?, ?B/s]

Upload file data/shard-027.parquet:  50%|####9     | 32.0k/64.5k [00:00<?, ?B/s]

Upload file data/shard-010.parquet:  51%|#####1    | 32.0k/62.4k [00:00<?, ?B/s]

Upload file data/shard-004.parquet: 100%|##########| 26.4k/26.4k [00:00<?, ?B/s]

To https://huggingface.co/datasets/nikolina-p/mini_gutenberg_tokenized
   21bb2c7..b60b62f  main -> main

   21bb2c7..b60b62f  main -> main



In [ ]:
mini_tokenized = load_dataset("nikolina-p/mini_gutenberg_tokenized", split="train")
mini_tokenized

README.md:   0%|          | 0.00/964 [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

shard-013.parquet:   0%|          | 0.00/212k [00:00<?, ?B/s]

shard-007.parquet:   0%|          | 0.00/637k [00:00<?, ?B/s]

shard-009.parquet:   0%|          | 0.00/393k [00:00<?, ?B/s]

...

shard-032.parquet:   0%|          | 0.00/244k [00:00<?, ?B/s]

shard-036.parquet:   0%|          | 0.00/258k [00:00<?, ?B/s]

shard-034.parquet:   0%|          | 0.00/408k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/117 [00:00<?, ? examples/s]

Dataset({
    features: ['id', 'text', 'tokenized'],
    num_rows: 117
})

In [ ]:
tok_num = 0
for e in mini_tokenized:
    tok_num += len(e["tokenized"])

print(f"NUMBER OF TOKENS IN MINI_GUTENBERG_TOKENIZED: {tok_num:,}")

NUMBER OF TOKENS IN MINI_GUTENBERG_TOKENIZED: 2,110,010


## **Mini Gutenberg: clean and splits**

In [ ]:
# import
from datasets import load_dataset, DownloadConfig
import os
from tqdm import tqdm
import shutil

In [ ]:
# download shard files
os.makedirs("my_dataset_cache", exist_ok=True)

for i in range(39):
    url = f"https://huggingface.co/datasets/nikolina-p/mini_gutenberg/resolve/main/data/shard-{i:03d}.parquet"
    !wget -P /content/my_dataset_cache/ {url}
    # os.system(f"wget -P /content {url}")

--2025-08-20 16:49:18--  https://huggingface.co/datasets/nikolina-p/mini_gutenberg/resolve/main/data/shard-000.parquet
Resolving huggingface.co (huggingface.co)... 18.239.50.16, 18.239.50.103, 18.239.50.49, ...
Connecting to huggingface.co (huggingface.co)|18.239.50.16|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs-us-1.hf.co/repos/ef/e5/efe56c725c6b7e0561577cd25a004fa326efb6de5db901a649ba071f1b30b280/9592e0e2e83e406847cf7c88bda67088dced910a2538a0fadd6fd793ae8df668?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27shard-000.parquet%3B+filename%3D%22shard-000.parquet%22%3B&Expires=1755712159&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTc1NTcxMjE1OX19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy11cy0xLmhmLmNvL3JlcG9zL2VmL2U1L2VmZTU2YzcyNWM2YjdlMDU2MTU3N2NkMjVhMDA0ZmEzMjZlZmI2ZGU1ZGI5MDFhNjQ5YmEwNzFmMWIzMGIyODAvOTU5MmUwZTJlODNlNDA2ODQ3Y2Y3Yzg4YmRhNjcwODhkY2VkOTEwYTI1MzhhMGZhZGQ2ZmQ3OTNhZThkZjY

In [ ]:
# split shards into train/test/valid => run the cell
parquet_dir = "my_dataset_cache"
parquet_files = sorted(f for f in os.listdir(parquet_dir) if f.endswith(".parquet"))
n = len(parquet_files)
train_files = parquet_files[:int(0.85 * n)]
val_files   = parquet_files[int(0.85 * n):int(0.95 * n)]
test_files  = parquet_files[int(0.95 * n):]

dataset_dir = os.makedirs("new_dir", exist_ok=True)
new_dir = "new_dir"
for split in ["train", "validation", "test"]:
    os.makedirs(os.path.join(new_dir, split), exist_ok=True)

# Copy files
for fname in train_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "train", fname))
for fname in val_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "validation", fname))
for fname in test_files:
    shutil.copy(os.path.join(parquet_dir, fname), os.path.join(new_dir, "test", fname))

In [ ]:
# upload dataset to HF Hub (LOGIN TO HUB FIRST)
upload_to_hf("nikolina-p/mini_gutenberg_splits", "new_dir")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, 

Upload file data/train/shard-007.parquet:   9%|9         | 32.0k/354k [00:00<?, ?B/s]

Upload file data/train/shard-009.parquet:  15%|#4        | 32.0k/220k [00:00<?, ?B/s]

Upload file data/train/shard-008.parquet:  15%|#4        | 32.0k/217k [00:00<?, ?B/s]

Upload file data/validation/shard-034.parquet:  15%|#5        | 32.0k/212k [00:00<?, ?B/s]

...

Upload file data/train/shard-003.parquet:  78%|#######8  | 32.0k/41.0k [00:00<?, ?B/s]

Upload file data/train/shard-027.parquet:  94%|#########3| 32.0k/34.1k [00:00<?, ?B/s]

Upload file data/train/shard-010.parquet: 100%|##########| 31.3k/31.3k [00:00<?, ?B/s]

Upload file data/train/shard-004.parquet: 100%|##########| 13.7k/13.7k [00:00<?, ?B/s]

To https://huggingface.co/datasets/nikolina-p/mini_gutenberg_splits
   0749a40..12e35fd  main -> main

   0749a40..12e35fd  main -> main



In [ ]:
from datasets import load_dataset
ds = load_dataset("nikolina-p/mini_gutenberg", split="train", streaming=True)
print(next(iter(ds)))

README.md:   0%|          | 0.00/863 [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/39 [00:00<?, ?it/s]

{'id': '41496-8', 'text': 'E-text prepared by the Online Distributed Proofreading Team (http://www.pgdp.net) from page images generously made available by Internet Archive (http://archive.org)\n\nNote: Images of the original pages are available through  Internet Archive. See  http://archive.org/details/addison_00cour\n\nTranscriber\'s note:\n\n Text enclosed by underscores is in italics (_italics_).\n\n Text enclosed by curly brackets is superscripted  (example: y{e}).\n\nEnglish Men of Letters\n\nEdited by John Morley\n\nADDISON\n\nby\n\nW. J. COURTHOPE\n\nHarper & Brothers Publishers New York and London 1902\n\n * * * * *\n\nENGLISH MEN OF LETTERS.\n\nEDITED BY JOHN MORLEY.\n\n JOHNSON Leslie Stephen.  GIBBON J. C. Morison.  SCOTT R. H. Hutton.  SHELLEY J. A. Symonds.  HUME T. H. Huxley.  GOLDSMITH William Black.  DEFOE William Minto.  BURNS J. C. Shairp.  SPENSER R. W. Church.  THACKERAY Anthony Trollope.  BURKE John Morley.  MILTON Mark Pattison.  HAWTHORNE Henry James, Jr.  SOUTHE

## test: Check duplicate books in manu/project_gutenberg

In [ ]:
from datasets import load_dataset

ds = load_dataset("manu/project_gutenberg", split="en", streaming=True)

stream = iter(ds)

Resolving data files:   0%|          | 0/52 [00:00<?, ?it/s]

In [ ]:
count = []
previous_id, previous_text = None, ""
stream_b = iter(ds)

while len(count) < 20:
    book = next(stream_b)
    book_id, book_text = book["id"], book["text"]

    if book_id == previous_id:
        dupl = {
            "id": book_id,
            "dupl": book_text == previous_text,
        }
        count.append(dupl)

    previous_id, previous_text = book_id, book_text

In [ ]:
count

[{'id': '41496-8', 'dupl': True},
 {'id': '25056-8', 'dupl': True},
 {'id': '48941-8', 'dupl': True},
 {'id': '35338-8', 'dupl': True},
 {'id': '21060-8', 'dupl': True},
 {'id': '22782-8', 'dupl': True},
 {'id': '59467-8', 'dupl': True},
 {'id': '18503-8', 'dupl': True},
 {'id': '30837-8', 'dupl': True},
 {'id': '14456-8', 'dupl': True},
 {'id': '18449-8', 'dupl': True},
 {'id': '36297-8', 'dupl': True},
 {'id': '31200-8', 'dupl': True},
 {'id': '57826-8', 'dupl': True},
 {'id': '24551-8', 'dupl': True},
 {'id': '28570-8', 'dupl': True},
 {'id': '13504-8', 'dupl': True},
 {'id': '39477-8', 'dupl': True},
 {'id': '26954-8', 'dupl': True},
 {'id': '49411-8', 'dupl': True}]

## ...